# PR0403

In [37]:
!hdfs dfs -mkdir /server-logs
!hdfs dfs -put pr0403/logfiles.log /server-logs
!hdfs dfs -ls /server-logs

mkdir: `/server-logs': File exists
put: `/server-logs/logfiles.log': File exists
Found 1 items
-rw-r--r--   3 root supergroup  241981538 2025-12-06 17:05 /server-logs/logfiles.log


## Ejercicio1

### Contador de códigos HTTP

In [38]:
%%writefile pr0403/ejercicio1/mapper_status_code.py
#!/usr/bin/env python3

import sys

for line in sys.stdin:
    if len(line) == 0:
        continue
    status_code = line.split(" ")
    if len(status_code) < 9:
        continue
    print(f"({status_code[8]}\t1)")

Writing pr0403/ejercicio1/mapper_status_code.py


In [39]:
%%writefile pr0403/ejercicio1/reducer_status_code.py
#!/usr/bin/env python3
import sys

current_code = None
current_count = 0

for line in sys.stdin:
    status, _ = line.strip().split("\t")
    if status == current_code:
        current_count += 1
    else:
        if current_code != None:
            print(f"{current_code}\t{current_count})")
        current_code = status
        current_count = 1

if current_code != None:
    print(f"{current_code}\t{current_count})")

Writing pr0403/ejercicio1/reducer_status_code.py


In [40]:
!cat pr0403/logfiles.log | python3 pr0403/ejercicio1/mapper_status_code.py | sort | python3 pr0403/ejercicio1/reducer_status_code.py

(200	142564)
(303	142261)
(304	143337)
(403	143014)
(404	142539)
(500	142729)
(502	143556)


In [41]:
!hdfs dfs -rm /processed/status_code/*
!hdfs dfs -rmdir /processed/status_code/
!hadoop jar \
/usr/local/hadoop/share/hadoop/tools/lib/hadoop-streaming-3.4.0.jar \
-file pr0403/ejercicio1/mapper_status_code.py \
-mapper pr0403/ejercicio1/mapper_status_code.py \
-file pr0403/ejercicio1/reducer_status_code.py \
-reducer pr0403/ejercicio1/reducer_status_code.py \
-input /server-logs/logfiles.log \
-output /processed/status_code
!hdfs dfs -cat /processed/status_code/part-00000

rm: `/processed/status_code/*': No such file or directory
rmdir: `/processed/status_code/': No such file or directory
2025-12-06 17:53:52,472 WARN streaming.StreamJob: -file option is deprecated, please use generic option -files instead.
packageJobJar: [pr0403/ejercicio1/mapper_status_code.py, pr0403/ejercicio1/reducer_status_code.py, /tmp/hadoop-unjar6543314492998903802/] [] /tmp/streamjob8112986979614796158.jar tmpDir=null
2025-12-06 17:53:52,910 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:53:52,983 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:53:53,131 INFO mapreduce.JobResourceUploader: Disabling Erasure Coding for path: /tmp/hadoop-yarn/staging/root/.staging/job_1765040352695_0005
2025-12-06 17:53:53,387 INFO mapred.FileInputFormat: Total input files to process : 1
2025-12-06 17:53:53,397 INFO net.NetworkTopology: Adding a new

### Tráfico total por IP

In [42]:
%%writefile pr0403/ejercicio1/mapper_ip.py
#!/usr/bin/env python3
import sys

for line in sys.stdin:
    if len(line) == 0:
        continue
    status_code = line.split(" ")
    if len(status_code) < 10:
        continue
    print(f"({status_code[0]}\t{status_code[9]})")

Writing pr0403/ejercicio1/mapper_ip.py


In [43]:
%%writefile pr0403/ejercicio1/reducer_ip.py
#!/usr/bin/env python3
import sys

current_ip = None
current_bytes_count = 0
for line in sys.stdin:
    ip, bytes_count = line.strip().split("\t")
    ip = ip.split("(")[1]
    bytes_count = int(bytes_count.split(")")[0])
    if ip == current_ip:
        current_bytes_count += bytes_count
    else:
        if current_ip:
            print(f"({current_ip}\t{current_bytes_count})")
        current_ip = ip
        current_bytes_count = bytes_count
if current_ip:
    print(f"({current_ip}\t{current_bytes_count})")



Writing pr0403/ejercicio1/reducer_ip.py


In [44]:
!cat pr0403/logfiles.log | python3 pr0403/ejercicio1/mapper_ip.py | sort | python3 pr0403/ejercicio1/reducer_ip.py

(0.0.106.234	4998)
(0.0.116.227	4927)
(0.0.142.71	4936)
(0.0.144.143	5030)
(0.0.201.132	4945)
(0.0.213.195	4917)
(0.0.253.11	5036)
(0.0.36.22	4996)
(0.0.47.93	4910)
(0.0.7.115	4951)
(0.0.71.76	5028)
(0.0.87.207	4975)
(0.0.94.174	5093)
(0.1.1.75	5008)
(0.1.122.253	4983)
(0.1.193.166	4996)
(0.1.221.62	4972)
(0.1.230.154	5028)
(0.1.236.188	4971)
(0.1.242.149	4962)
(0.1.254.162	4921)
(0.1.5.80	4951)
(0.10.128.105	5040)
(0.10.137.129	4984)
(0.10.137.223	4981)
(0.10.154.78	4906)
(0.10.166.243	5022)
(0.10.181.9	5046)
(0.10.183.4	4913)
(0.10.189.37	5021)
(0.10.197.164	4981)
(0.10.203.205	5045)
(0.10.243.165	4976)
(0.10.37.229	4911)
(0.10.66.162	5038)
(0.10.85.36	5020)
(0.10.86.4	5041)
(0.100.110.37	4955)
(0.100.143.180	4982)
(0.100.156.70	4926)
(0.100.166.29	4966)
(0.100.18.185	4945)
(0.100.19.188	5065)
(0.100.248.212	5025)
(0.100.40.202	5053)
(0.100.49.184	5035)
(0.100.58.65	5089)
(0.100.67.120	5101)
(0.100.71.221	5055)
(0.100.80.218	5053)
(0.101.112.73	4961)
(0.101.135.35	4977)
(0.101.149.12

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [45]:
!hdfs dfs -rm /processed/ip_byte/*
!hdfs dfs -rmdir /processed/ip_byte/
!hadoop jar \
/usr/local/hadoop/share/hadoop/tools/lib/hadoop-streaming-3.4.0.jar \
-file pr0403/ejercicio1/mapper_ip.py \
-mapper pr0403/ejercicio1/mapper_ip.py \
-file pr0403/ejercicio1/reducer_ip.py \
-reducer pr0403/ejercicio1/reducer_ip.py \
-input /server-logs/logfiles.log \
-output /processed/ip_byte
!hdfs dfs -cat /processed/ip_byte/part-00000

rm: `/processed/ip_byte/*': No such file or directory
rmdir: `/processed/ip_byte/': No such file or directory
2025-12-06 17:54:16,421 WARN streaming.StreamJob: -file option is deprecated, please use generic option -files instead.
packageJobJar: [pr0403/ejercicio1/mapper_ip.py, pr0403/ejercicio1/reducer_ip.py, /tmp/hadoop-unjar8862957961388489392/] [] /tmp/streamjob3024117734644898830.jar tmpDir=null
2025-12-06 17:54:16,816 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:54:16,882 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:54:17,047 INFO mapreduce.JobResourceUploader: Disabling Erasure Coding for path: /tmp/hadoop-yarn/staging/root/.staging/job_1765040352695_0006
2025-12-06 17:54:17,321 INFO mapred.FileInputFormat: Total input files to process : 1
2025-12-06 17:54:17,332 INFO net.NetworkTopology: Adding a new node: /default-rack/172.1

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



`El ejercicio funciona, pero parece que jupyter pone un límite a la salida que puede mostrar`

## Ejercicio 2

### URLs más populares

In [46]:
%%writefile pr0403/ejercicio2/mapper_url.py
#!/usr/bin/env python3
import sys

current_url = None
current_count = 0
for line in sys.stdin:
    if len(line) == 0:
        continue
    info = line.split(" ")
    if len(info) < 7:
        continue
    if current_url == info[6]:
        current_count += 1
    else:
        if current_url:
            print(f"({current_url}\t{current_count})")
        current_url = info[6]
        current_count = 1
if current_url:
    print(f"({current_url}\t{current_count})")

Writing pr0403/ejercicio2/mapper_url.py


In [47]:
%%writefile pr0403/ejercicio2/reducer_url.py
#!/usr/bin/env python3
import sys

url_to_count = dict()

for line in sys.stdin:
    url, count = line.strip().split("\t")
    url = url.split("(")[1]
    count = int(count.split(")")[0])
    url_to_count[url] = url_to_count.get(url, 0) + count
sorted_urls = dict(sorted(url_to_count.items(), key=lambda x: 1/x[1]))
print(sorted_urls)

Writing pr0403/ejercicio2/reducer_url.py


In [48]:
!cat pr0403/logfiles.log | python3 pr0403/ejercicio2/mapper_url.py | sort | python3 pr0403/ejercicio2/reducer_url.py

{'/usr': 200383, '/usr/register': 200296, '/usr/login': 200225, '/usr/admin/developer': 200000, '/usr/admin': 199096}


In [49]:
!hdfs dfs -rm /processed/urls/*
!hdfs dfs -rmdir /processed/urls/
!hadoop jar \
/usr/local/hadoop/share/hadoop/tools/lib/hadoop-streaming-3.4.0.jar \
-file pr0403/ejercicio2/mapper_url.py \
-mapper pr0403/ejercicio2/mapper_url.py \
-file pr0403/ejercicio2/reducer_url.py \
-reducer pr0403/ejercicio2/reducer_url.py \
-input /server-logs/logfiles.log \
-output /processed/urls
!hdfs dfs -cat /processed/urls/part-00000

rm: `/processed/urls/*': No such file or directory
rmdir: `/processed/urls/': No such file or directory
2025-12-06 17:54:42,191 WARN streaming.StreamJob: -file option is deprecated, please use generic option -files instead.
packageJobJar: [pr0403/ejercicio2/mapper_url.py, pr0403/ejercicio2/reducer_url.py, /tmp/hadoop-unjar5997526174648341987/] [] /tmp/streamjob2017205415005089348.jar tmpDir=null
2025-12-06 17:54:42,672 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:54:42,748 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:54:42,919 INFO mapreduce.JobResourceUploader: Disabling Erasure Coding for path: /tmp/hadoop-yarn/staging/root/.staging/job_1765040352695_0007
2025-12-06 17:54:43,163 INFO mapred.FileInputFormat: Total input files to process : 1
2025-12-06 17:54:43,173 INFO net.NetworkTopology: Adding a new node: /default-rack/172.19.0.

Es bastante probable que esta implementación no hubiese funcionado si en el archivo de logs hubiera más urls, ya que es probable que hubiera hecho el `reduce` en más máquinas entonces, no se podrían juntar en un diccionario. Aún así, elegí aplicar heurística y dejar el código cómo está.

### Distribución por método HTTP

In [50]:
%%writefile pr0403/ejercicio2/mapper_metodo.py
#!/usr/bin/env python3
import sys

current_method = None
current_count = 0
for line in sys.stdin:
    method = line.strip().split(" ")[5]
    method = method.split("\"")[1]
    if method == current_method:
        current_count += 1
    else:
        if current_method:
            print(f"({current_method}\t{current_count})")
        current_method = method
        current_count = 1

if current_method:
    print(f"({current_method}\t{current_count})")

Writing pr0403/ejercicio2/mapper_metodo.py


In [51]:
%%writefile pr0403/ejercicio2/reducer_metodo.py
#!/usr/bin/env python3
import sys

current_method = None
current_count = 0
for line in sys.stdin:
    method, count = line.strip().split("\t")
    method = method.split("(")[1]
    count = int(count.split(")")[0])
    if method == current_method:
        current_count += count
    else:
        if current_method:
            print(f"({current_method}\t{current_count})")
        current_method = method
        current_count = count

if current_method:
    print(f"({current_method}\t{current_count})")

Writing pr0403/ejercicio2/reducer_metodo.py


In [52]:
!cat pr0403/logfiles.log | python3 pr0403/ejercicio2/mapper_metodo.py | sort | python3 pr0403/ejercicio2/reducer_metodo.py

(DELETE	249768)
(GET	250515)
(POST	248931)
(PUT	250786)


In [53]:
!hdfs dfs -rm /processed/methods/*
!hdfs dfs -rmdir /processed/methods/
!hadoop jar \
/usr/local/hadoop/share/hadoop/tools/lib/hadoop-streaming-3.4.0.jar \
-file pr0403/ejercicio2/mapper_metodo.py \
-mapper pr0403/ejercicio2/mapper_metodo.py \
-file pr0403/ejercicio2/reducer_metodo.py \
-reducer pr0403/ejercicio2/reducer_metodo.py \
-input /server-logs/logfiles.log \
-output /processed/methods
!hdfs dfs -cat /processed/methods/part-00000

rm: `/processed/methods/*': No such file or directory
rmdir: `/processed/methods/': No such file or directory
2025-12-06 17:55:04,187 WARN streaming.StreamJob: -file option is deprecated, please use generic option -files instead.
packageJobJar: [pr0403/ejercicio2/mapper_metodo.py, pr0403/ejercicio2/reducer_metodo.py, /tmp/hadoop-unjar1568842331881632647/] [] /tmp/streamjob2114643114601340814.jar tmpDir=null
2025-12-06 17:55:04,640 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:55:04,719 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:55:04,902 INFO mapreduce.JobResourceUploader: Disabling Erasure Coding for path: /tmp/hadoop-yarn/staging/root/.staging/job_1765040352695_0008
2025-12-06 17:55:05,182 INFO mapred.FileInputFormat: Total input files to process : 1
2025-12-06 17:55:05,193 INFO net.NetworkTopology: Adding a new node: /default-ra

### Ánalisis de navegadores

`Código con muchas optimizaciones`

In [54]:
%%writefile pr0403/ejercicio2/mapper_browser.py
#!/usr/bin/env python3
import sys 
import re
excluded = set([b'NT', b'like', b'lik', b'Gecko)', b'ONEPLUS', b'X', b'Intel', b'OS', b'Mac', b'Android', b'CPU', b'iPhone', b'IPhone', b'Mobile', b'Version'])
regex = re.compile(b'[;(){}0-9]')
buffer = []
BUFFER_LIMIT = 50000
for line in sys.stdin.buffer:
    browsers = line.strip().rsplit(b"\"", 2)[-2]
    for browser in browsers.split():
        browser_name = browser.split(b"/")[0]
        if browser_name in excluded:
            continue
        if regex.search(browser_name):
            continue
        buffer.append(f"({browser_name.decode('utf-8')}\t1)")
        if len(buffer) >= BUFFER_LIMIT:
            print("\n".join(buffer))
            buffer = []
if len(buffer) > 0:
    print("\n".join(buffer))
    

Writing pr0403/ejercicio2/mapper_browser.py


In [55]:
%%writefile pr0403/ejercicio2/reducer_browser.py
#!/usr/bin/env python3
import sys

current_browser = None
current_count = 0
buffer = []
BUFFER_LIMIT = 50000
for line in sys.stdin.buffer:
    browser, count = line.strip().split(b"\t")
    browser = browser.split(b"(")[1].decode('utf-8')
    count = int(count.split(b")")[0].decode('utf-8'))
    if browser == current_browser:
        current_count += count
    else:
        if current_browser:
            buffer.append(f"({current_browser}\t{current_count})")
            if len(buffer) >= BUFFER_LIMIT:
                print("\n".join(buffer))
                buffer = []
        current_browser = browser
        current_count = 0
buffer.append(f"({current_browser}\t{current_count})")
if len(buffer) > 0:
    print("\n".join(buffer))
    



Writing pr0403/ejercicio2/reducer_browser.py


In [56]:
!cat pr0403/logfiles.log | python3 pr0403/ejercicio2/mapper_browser.py | sort | python3 pr0403/ejercicio2/reducer_browser.py

(AppleWebKit	800046)
(Chrome	599508)
(Edg	99435)
(EdgA	100023)
(Firefox	199952)
(Gecko	199952)
(Mozilla	999999)
(OPR	200428)
(Safari	800046)


In [57]:
!hdfs dfs -rm /processed/browsers/*
!hdfs dfs -rmdir /processed/browsers/
!hadoop jar \
/usr/local/hadoop/share/hadoop/tools/lib/hadoop-streaming-3.4.0.jar \
-file pr0403/ejercicio2/mapper_browser.py \
-mapper pr0403/ejercicio2/mapper_browser.py \
-file pr0403/ejercicio2/reducer_browser.py \
-reducer pr0403/ejercicio2/reducer_browser.py \
-input /server-logs/logfiles.log \
-output /processed/browsers
!hdfs dfs -cat /processed/browsers/part-00000


Deleted /processed/browsers/_SUCCESS
Deleted /processed/browsers/part-00000
2025-12-06 17:55:33,246 WARN streaming.StreamJob: -file option is deprecated, please use generic option -files instead.
packageJobJar: [pr0403/ejercicio2/mapper_browser.py, pr0403/ejercicio2/reducer_browser.py, /tmp/hadoop-unjar2459062260484226310/] [] /tmp/streamjob4545284864399339644.jar tmpDir=null
2025-12-06 17:55:33,685 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:55:33,765 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:55:33,933 INFO mapreduce.JobResourceUploader: Disabling Erasure Coding for path: /tmp/hadoop-yarn/staging/root/.staging/job_1765040352695_0009
2025-12-06 17:55:34,186 INFO mapred.FileInputFormat: Total input files to process : 1
2025-12-06 17:55:34,196 INFO net.NetworkTopology: Adding a new node: /default-rack/172.19.0.2:9866
2025-12-06 17

## Ejercicio 3

### Picos de tráfico por hora

In [58]:
%%writefile pr0403/ejercicio3/mapper_hour.py
#!/usr/bin/env python3
import sys
current_hour = None
current_count = 0
buffer = []
BUFFER_LIMIT = 50000

for line in sys.stdin.buffer:
    hour = line.strip().split(b" ")[3].split(b":")[1].decode('utf-8')
    if hour == current_hour:
        current_count += 1
    else:
        if current_hour:
            buffer.append(f"({current_hour}\t{current_count})")
            if len(buffer) >= BUFFER_LIMIT:
                print("\n".join(buffer))
                buffer = []
        current_hour = hour
        current_count = 1
if current_hour:
    buffer.append(f"({current_hour}\t{current_count})")
    print("\n".join(buffer))

Writing pr0403/ejercicio3/mapper_hour.py


In [59]:
%%writefile pr0403/ejercicio3/reducer_hour.py
#!/usr/bin/env python3
import sys
current_hour = None
current_count = 0
buffer = []
BUFFER_LIMIT = 50000

for line in sys.stdin.buffer:
    hour, count = line.strip().split(b"\t")
    hour = hour.split(b"(")[1].decode("utf-8")
    count = int(count.split(b")")[0].decode("utf-8"))
    if hour == current_hour:
        current_count += count
    else:
        if current_hour:
            buffer.append(f"({current_hour}\t{current_count})")
            if len(buffer) >= BUFFER_LIMIT:
                print("\n".join(buffer))
                buffer = []
        current_hour = hour
        current_count = count
if current_hour:
    buffer.append(f"({current_hour}\t{current_count})")
    print("\n".join(buffer))

Writing pr0403/ejercicio3/reducer_hour.py


In [60]:
!cat pr0403/logfiles.log | python3 pr0403/ejercicio3/mapper_hour.py | sort | python3 pr0403/ejercicio3/reducer_hour.py

(12	1000000)


In [61]:
!hdfs dfs -rm /processed/hours/*
!hdfs dfs -rmdir /processed/hours/
!hadoop jar \
/usr/local/hadoop/share/hadoop/tools/lib/hadoop-streaming-3.4.0.jar \
-file pr0403/ejercicio3/mapper_hour.py \
-mapper pr0403/ejercicio3/mapper_hour.py \
-file pr0403/ejercicio3/reducer_hour.py \
-reducer pr0403/ejercicio3/reducer_hour.py \
-input /server-logs/logfiles.log \
-output /processed/hours
!hdfs dfs -cat /processed/hours/part-00000


Deleted /processed/hours/_SUCCESS
Deleted /processed/hours/part-00000
2025-12-06 17:55:59,719 WARN streaming.StreamJob: -file option is deprecated, please use generic option -files instead.
packageJobJar: [pr0403/ejercicio3/mapper_hour.py, pr0403/ejercicio3/reducer_hour.py, /tmp/hadoop-unjar2295064303333543131/] [] /tmp/streamjob4796406101335929712.jar tmpDir=null
2025-12-06 17:56:00,157 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:56:00,228 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:56:00,405 INFO mapreduce.JobResourceUploader: Disabling Erasure Coding for path: /tmp/hadoop-yarn/staging/root/.staging/job_1765040352695_0010
2025-12-06 17:56:00,664 INFO mapred.FileInputFormat: Total input files to process : 1
2025-12-06 17:56:00,674 INFO net.NetworkTopology: Adding a new node: /default-rack/172.19.0.2:9866
2025-12-06 17:56:00,674 I

### Tasa de error por endpoint

In [62]:
%%writefile pr0403/ejercicio3/mapper_error.py
#!/usr/bin/env python3
import sys
buffer = []
BUFFER_LIMIT = 50000

for line in sys.stdin.buffer:
    if len(line) == 0:
        continue
    split = line.strip().split(b' ')
    url = split[6].decode('utf-8')
    result = 1 if int(split[8].decode('utf-8')) >= 400 else 0
    buffer.append(f"({url}\t{result})")
    if len(buffer) >= BUFFER_LIMIT:
        print("\n".join(buffer))
        buffer = []
if len(buffer) > 0:
    print("\n".join(buffer))

Writing pr0403/ejercicio3/mapper_error.py


In [63]:
%%writefile pr0403/ejercicio3/reducer_error.py
#!/usr/bin/env python3
import sys

current_url = None
current_error = 0
current_count = 0

buffer = []
BUFFER_LIMIT = 50000

for line in sys.stdin.buffer:
    url, result = line.strip().split(b'\t')
    url = url.split(b'(')[1].decode('utf-8')
    result = bool(int(result.split(b')')[0].decode('utf-8')))
    if url == current_url:
        current_count += 1
        if not result:
            current_error += 1
    else:
        if current_url:
            buffer.append(f"({current_url}\t{current_error / current_count * 100}%)")
            if len(buffer) > BUFFER_LIMIT:
                print("\n".join(buffer))
                buffer = []
        current_url = url
        current_count = 1
        current_error = 1 if result else 0
if current_url:
    buffer.append(f"({current_url}\t{current_error / current_count * 100}%)")
    print("\n".join(buffer))



Writing pr0403/ejercicio3/reducer_error.py


In [64]:
!cat pr0403/logfiles.log | python3 pr0403/ejercicio3/mapper_error.py | sort | python3 pr0403/ejercicio3/reducer_error.py

(/usr	42.746141139717444%)
(/usr/admin	42.80748985414072%)
(/usr/admin/developer	42.949%)
(/usr/login	42.690473217630164%)
(/usr/register	42.88552941646363%)


In [65]:
!hdfs dfs -rm /processed/error/*
!hdfs dfs -rmdir /processed/error/
!hadoop jar \
/usr/local/hadoop/share/hadoop/tools/lib/hadoop-streaming-3.4.0.jar \
-file pr0403/ejercicio3/mapper_error.py \
-mapper pr0403/ejercicio3/mapper_error.py \
-file pr0403/ejercicio3/reducer_error.py \
-reducer pr0403/ejercicio3/reducer_error.py \
-input /server-logs/logfiles.log \
-output /processed/error
!hdfs dfs -cat /processed/error/part-00000


Deleted /processed/error/_SUCCESS
Deleted /processed/error/part-00000
2025-12-06 17:56:22,231 WARN streaming.StreamJob: -file option is deprecated, please use generic option -files instead.
packageJobJar: [pr0403/ejercicio3/mapper_error.py, pr0403/ejercicio3/reducer_error.py, /tmp/hadoop-unjar1037394132853226036/] [] /tmp/streamjob2424972003326423235.jar tmpDir=null
2025-12-06 17:56:22,669 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:56:22,750 INFO client.DefaultNoHARMFailoverProxyProvider: Connecting to ResourceManager at yarnmanager/172.19.0.5:8032
2025-12-06 17:56:22,928 INFO mapreduce.JobResourceUploader: Disabling Erasure Coding for path: /tmp/hadoop-yarn/staging/root/.staging/job_1765040352695_0011
2025-12-06 17:56:23,204 INFO mapred.FileInputFormat: Total input files to process : 1
2025-12-06 17:56:23,217 INFO net.NetworkTopology: Adding a new node: /default-rack/172.19.0.2:9866
2025-12-06 17:56:23,217